In [3]:
import json
import pandas as pd
import geopandas as gpd
import folium
from folium import GeoJsonTooltip
import ipywidgets as widgets
from IPython.display import display, clear_output
import math


#### Plot the whole NE data that has been filtered by the rule_base_filtering.py with hovering labels

In [4]:
# Load the GeoJSON file
with open('../output/final_data.geojson') as f:
    nb = json.load(f)
nb_predictions = folium.Map(location=[41.5, -100], zoom_start=7)
folium.GeoJson(nb).add_to(nb_predictions)

# Add Esri Satellite tile layer
tile = folium.TileLayer(
        tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
        attr = 'Esri',
        name = 'Esri Satellite',
        overlay = False,
        control = True
       ).add_to(nb_predictions)

# Sort features within the GeoJSON data by longitude for standardized processing
features_with_lon = [(feature, feature['geometry']['coordinates'][0][0][0]) for feature in nb['features']]
features_with_lon.sort(key=lambda x: x[1])

# Assign an index property to each feature based on its sorted position
for index, (feature, _) in enumerate(features_with_lon):
    feature['properties']['index'] = index

# Update the features in the GeoJSON data with their new indices and sorted order
nb['features'] = [feature for feature, _ in features_with_lon]

# Add additional properties (latitude and longitude of the first point) to each feature for use in tooltips
for feature in nb['features']:
    first_point = feature['geometry']['coordinates'][0][0]
    feature['properties']['first_point_lon'] = first_point[0]
    feature['properties']['first_point_lat'] = first_point[1]

# Define a GeoJsonTooltip that will display the index, latitude, longitude, and distance to the nearest road when hovering over a feature
geojson_tooltip = GeoJsonTooltip(
    fields=['index', 'first_point_lat', 'first_point_lon', 'distance_to_nearest_road'],
    aliases=['Index:', 'Latitude:', 'Longitude:', 'Distance to nearest road (meters):'],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

# Add the GeoJSON data with the tooltips to the folium map
folium.GeoJson(
    nb,
    tooltip=geojson_tooltip
).add_to(nb_predictions)

# Display the map
nb_predictions

#### Plot the data in a given area with hovering labels

In [5]:
# Assuming that the latitude and longitude bounds are defined as follows:
lat_min, lat_max = 40, 40.5
lon_min, lon_max = -100, -99.5

# Load the GeoJSON file
with open('../output/final_data.geojson') as f:
    nb = json.load(f)

# Create the map object
nb_predictions = folium.Map(location=[41.5, -100], zoom_start=7)

# Add Esri Satellite tile layer
tile = folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Esri',
    name='Esri Satellite',
    overlay=False,
    control=True
).add_to(nb_predictions)

# Extract longitude for sorting and sort features
features_with_lon = [(feature, feature['geometry']['coordinates'][0][0][0]) for feature in nb['features']]
features_with_lon.sort(key=lambda x: x[1])
for index, (feature, _) in enumerate(features_with_lon):
    feature['properties']['index'] = index
    # Assign first point lat and lon to each feature's properties
    first_point = feature['geometry']['coordinates'][0][0]
    feature['properties']['first_point_lon'] = first_point[0]
    feature['properties']['first_point_lat'] = first_point[1]

# Update the features list after sorting and adding properties
nb['features'] = [feature for feature, _ in features_with_lon]

# Filter features within the specified latitude and longitude bounds
filtered_features = [feature for feature in nb['features'] if lat_min <= feature['properties']['first_point_lat'] <= lat_max and lon_min <= feature['properties']['first_point_lon'] <= lon_max]

# Create GeoJsonTooltip with the correct fields
geojson_tooltip = GeoJsonTooltip(
    fields=['index', 'first_point_lat', 'first_point_lon', 'distance_to_nearest_road'],
    aliases=['Index:', 'Latitude:', 'Longitude:', 'Distance to nearest road (meters):'],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

# Add filtered features with tooltips to the map
folium.GeoJson(
    data={"type": "FeatureCollection", "features": filtered_features},
    tooltip=geojson_tooltip
).add_to(nb_predictions)

# Display the map
nb_predictions


#### Display checkboxes for all barn indexes in the given area

In [6]:
# Define the latitude and longitude range
lat_min, lat_max = 40, 40.5
lon_min, lon_max = -100, -99.5

# Filter features by getting the coordinates of the first point of the polygons
filtered_features = [feature for feature in nb['features'] 
                     if any(lat_min <= point[1] <= lat_max and 
                            lon_min <= point[0] <= lon_max 
                            for point in feature['geometry']['coordinates'][0])]

# Update global variables to reflect the filtered features
all_checkboxes = [widgets.Checkbox(value=False, description=str(feature['properties']['index'])) 
                  for feature in filtered_features if 'index' in feature['properties']]
checkbox_states = [cb.value for cb in all_checkboxes]

# Calculate the number of checkboxes per column
num_columns = 3
checkboxes_per_column = len(all_checkboxes) // num_columns + 1

# Create multiple columns to display the checkboxes
columns = [[] for _ in range(num_columns)]
for i, checkbox in enumerate(all_checkboxes):
    columns[i % num_columns].append(checkbox)

# Place each column in a VBox
column_boxes = [widgets.VBox(children=column) for column in columns]

# Create a grid layout to display the multiple columns of checkboxes
grid_layout = widgets.HBox(children=column_boxes)
display(grid_layout)

# Create the "Mark False Positives" button and event handling function
submit_button = widgets.Button(description="Mark False Positives")
display(submit_button)

# Event handling function for submit button click
def on_submit_clicked(b):
    # Clear the old map output
    clear_output(wait=True)
    # Redisplay the checkboxes and button
    display(grid_layout)
    display(submit_button)
    
    # Check which checkboxes are ticked and update checkbox_states
    for i, cb in enumerate(all_checkboxes):
        checkbox_states[i] = cb.value

    # Update the GeoJSON data based on the checkbox states
    updated_features = [feature for i, feature in enumerate(filtered_features) if not checkbox_states[i]]
    
    # Recreate the map and display points not marked as false positives
    new_map = folium.Map(location=[41.5, -100], zoom_start=7)
    folium.GeoJson({"type": "FeatureCollection", "features": updated_features}).add_to(new_map)
    
    # Add Esri Satellite tile layer
    tile = folium.TileLayer(
        tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
        attr='Esri',
        name='Esri Satellite',
        overlay=False,
        control=True
    )
    tile.add_to(new_map)  # Correctly adding the tile layer to the new map object

    display(new_map)

submit_button.on_click(on_submit_clicked)


Button(description='Mark False Positives', style=ButtonStyle())

#### Save the filtered data with no false positives to a new GeoJSON file

In [7]:
# Filter features, keeping only those not marked as false positives
filtered_features = [feature for feature, state in zip(nb['features'], checkbox_states) if not state]

# Create a new GeoJSON object, containing only the retained features
filtered_geojson = {
    "type": "FeatureCollection",
    "features": filtered_features
}

# Write the filtered GeoJSON to a file
output_file_path = "../output/final_data_NE_noFP.geojson"  # Specify the output file path
with open(output_file_path, 'w') as outfile:
    json.dump(filtered_geojson, outfile)

print(f"Filtered GeoJSON saved to {output_file_path}")

num_features = len(filtered_features)
print(f"Filtered GeoJSON file contains {num_features} lines.")


Filtered GeoJSON saved to ../output/final_data_NE_noFP.geojson
Filtered GeoJSON file contains 93 lines.


In [13]:
print(geojson_data['features'][0]['properties'])


{'p': 0.6050846862042308, 'rectangle_area': 954.723243228165, 'area': 751.0, 'rectangle_aspect_ratio': 3.786237188922533, 'distance_to_nearest_road': 3.893789887420299, 'year': 2017, 'date': '2017-7-31', 'image_url': 'https://naipblobs.blob.core.windows.net/naip/v002/co/2017/co_100cm_2017/41102/m_4110257_se_13_1_20170731.tif', 'Nebraska': True}


In [8]:
from ipyleaflet import Map, GeoJSON, WidgetControl, TileLayer
from ipywidgets import HTML, Layout
import json
import threading
import time
# Load your GeoJSON data
with open('../output/final_data.geojson') as f:
    geojson_data = json.load(f)
for i, feature in enumerate(geojson_data['features']):
    # Assign an 'index' property to each feature
    feature['properties']['index'] = i
# Initialize the map
m = Map(center=(41.5, -100), zoom=7)
# Widget to display feature information on the map
widget = HTML()
widget.layout.margin = '0px 20px 20px 20px'
control = WidgetControl(widget=widget, position='bottomright')
m.add_control(control)
# Global variable to keep track of hover state
is_hovering = False
is_clicking = False
# Define a hover handler
def handle_hover(event, feature, **kwargs):
    global is_hovering
    is_hovering = True
    properties = feature['properties']
    geometry = feature['geometry']['coordinates'][0][0]
    longitude, latitude = geometry[:2]
    index = feature['properties']['index']
    # Update the widget to show information
    widget.value = f'Index: {index}, Lat: {latitude}, Lon: {longitude}'
def handle_click(event, feature, **kwargs):
    global is_hovering
    is_clicking = True
    print("Click event triggered")  # Debugging line to ensure the function is called
    index = feature['properties']['index']
    print(f'Feature Index: {index}')
# Function to clear the widget if not hovering
def clear_widget(*args, **kwargs):
    global is_hovering
    if not is_hovering:
        widget.value = ''
    is_hovering = False
# Create the GeoJSON layer with hover functionality and add it to the map
geo_json = GeoJSON(
    data=geojson_data,
    style={'color': 'blue', 'opacity': 0.5},
    hover_style={'color': 'green', 'fillOpacity': 0.8}
)
geo_json.on_click(handle_click)
#geo_json.on_hover(handle_hover)

# Add Esri Satellite tile layer
esri_satellite = TileLayer(
    url='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attribution='Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community'
)
m.add_layer(esri_satellite)

m.add_layer(geo_json)
m

Map(center=[41.5, -100], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out…